In [1]:
import pandas as pd
import numpy as np
import lightfm
from lightfm import LightFM
from lightfm.evaluation import precision_at_k, recall_at_k, reciprocal_rank, auc_score
from lightfm.cross_validation import random_train_test_split
from dataloading import DataLoader
from datapreparation_py import DataPreparation
from lightFM_adoptor import LightFMAdaptor
from cv_py import CrossValidation
from implicit.evaluation import ranking_metrics_at_k, train_test_split

c:\Users\781110104\Anaconda3\lib\site-packages\lightfm\_lightfm_fast.py:9: UserWarning: LightFM was compiled without OpenMP support. Only a single thread will be used.
  warnings.warn(


In [2]:
%cd C:\Users\781110104\OneDrive - Genpact\Documents\VSCode

C:\Users\781110104\OneDrive - Genpact\Documents\VSCode


In [3]:
dl = DataLoader()
user_item_co_t = dl.import_data('TEREX', 'CO', 'df')

In [4]:
user_item_co_t_filtered = dl.remove_low_interact_items(user_item_co_t, 1)

In [5]:
user_item_filtered_log_t = dl.log_scale_df(user_item_co_t_filtered, 0.01)

In [6]:
dp = DataPreparation(user_item_filtered_log_t)

In [7]:
interactions_csr, weights_csr = dp.get_interaction_data()

In [28]:
from scipy import sparse
sparse.save_npz('interactions_csr_t.npz', interactions_csr)
sparse.save_npz('weights_csr_t.npz', weights_csr)

In [16]:
user_features = ['country', 'brand', 'currency']
item_features = ['group2', 'movement_code', 'cost_class']
feature_input = dp.get_feature_data(OEM='TEREX', user_features=user_features, item_features=item_features)

In [17]:
userf, itemf = feature_input

In [18]:
user_features = ['country']
item_features = ['group2']
userf_country, itemf_group2 = dp.get_feature_data(OEM='TEREX', user_features=user_features, item_features=item_features)

In [19]:
user_features = ['brand']
item_features = ['movement_code']
userf_brand, itemf_move = dp.get_feature_data(OEM='TEREX', user_features=user_features, item_features=item_features)

In [20]:
user_features = ['currency']
item_features = ['cost_class']
userf_curr, itemf_cost = dp.get_feature_data(OEM='TEREX', user_features=user_features, item_features=item_features)

In [9]:
user_features = ['country', 'brand']
item_features = ['group2', 'movement_code']
userf_country_brand, itemf_group2_move = dp.get_feature_data(OEM='TEREX', user_features=user_features, item_features=item_features)

In [21]:
user_features = ['country', 'currency']
item_features = ['group2', 'cost_class']
userf_country_curr, itemf_group2_cost = dp.get_feature_data(OEM='TEREX', user_features=user_features, item_features=item_features)

In [22]:
user_features = ['brand', 'currency']
item_features = ['movement_code', 'cost_class']
userf_brand_curr, itemf_move_cost = dp.get_feature_data(OEM='TEREX', user_features=user_features, item_features=item_features)

In [29]:
sparse.save_npz('itemf_move_cost_t.npz', itemf_move_cost[0])
sparse.save_npz('itemf_group_cost_t.npz', itemf_group2_cost[0])
sparse.save_npz('itemf_group_move_t.npz', itemf_group2_move[0])
sparse.save_npz('itemf_cost_t.npz', itemf_cost[0])
sparse.save_npz('itemf_move_t.npz', itemf_move[0])
sparse.save_npz('itemf_group_t.npz', itemf_group2[0])
sparse.save_npz('itemf_t.npz', itemf)

In [30]:
sparse.save_npz('userf_t.npz', userf)
sparse.save_npz('userf_country_t.npz', userf_country[0])
sparse.save_npz('userf_curr_t.npz', userf_curr[0])
sparse.save_npz('userf_ds_t.npz', userf_brand[0])
sparse.save_npz('userf_country_curr_t.npz', userf_country_curr[0])
sparse.save_npz('userf_country_ds_t.npz', userf_country_brand[0])
sparse.save_npz('userf_curr_ds_t.npz', userf_brand_curr[0])

In [10]:
train_i, test_i = train_test_split(interactions_csr, 0.8, 22)
train_w, test_w = train_test_split(weights_csr, 0.8, 22)

In [11]:
cal_w, val_w = train_test_split(train_w, 0.8, 22)
cal_i, val_i = train_test_split(train_i, 0.8, 22)

In [12]:
cv = CrossValidation(5)

Testing the model with simple parameter tuning:

First with WARP loss:

In [23]:
space_FM_warp = {'factors' : [40], 'regularization' : [0.005], 
'learning_rate' : [0.1], 'iterations' : [10], 'loss' : ['warp'], 'max_sampled' : [40]}

uf_combi = [None, userf_country, userf_brand, userf_curr, userf_country_brand, userf_country_curr, userf_brand_curr, userf]
if_combi = [None, itemf_group2, itemf_move, itemf_cost, itemf_group2_move, itemf_group2_cost, itemf_move_cost, itemf]

uf_names = ['None', 'userf_country', 'userf_brand', 'userf_curr', 'userf_country_brand', 'userf_country_curr', 'userf_brand_curr', 'userf']
if_names = ['None', 'itemf_group2', 'itemf_move', 'itemf_cost', 'itemf_group2_move', 'itemf_group2_cost', 'itemf_move_cost', 'itemf']

In [24]:
results_warp = cv.tune_FM(space=space_FM_warp, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, 
if_names=if_names, train=cal_w, test=val_w, exclude=test_w)

In [26]:
results_warp.sort_values('precision', ascending=False).head(10)

factors  regularization  learning_rate  iterations  loss  max_sampled  \
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   
0       40           0.005            0.1          10  warp           40   

   precision       map      ndcg       auc       mpr              uf_name  \
0     0.4375  0.290300  0.441461  0.512131  0.176946                 None   
0     0.4150  0.276383  0.433602  0.511849  0.187027        userf_country   
0     0.4100  0.280269  0.440835  0.511375  0.192986                 None   
0     0.3900  0.230364  0.392308  0.511747  0.171405           userf_curr   
0     0.3675  0.230358  0.378455  0.510002  0.157221  userf_country_brand   
0     0.3625  0.233083  0.375404  0.509904  0.172345           userf_curr   
0     0.3625  0.236753  0.385280  0.509298  0.169239          userf_brand   
0     0.3525  0.221401  0.366486  0.509767  0.164035           userf_curr   
0     0.3525  0.208631  0.353928  0.509274  0.170962   userf_country_curr   
0     0.3500  0.211468  0.362842  0.509237  0.179373           userf_curr   

             if_name  
0  itemf_group2_move  
0         itemf_move  
0    itemf_move_cost  
0  itemf_group2_cost  
0       itemf_group2  
0         itemf_move  
0         itemf_move  
0         itemf_cost  
0       itemf_group2  
0       itemf_group2

In [21]:
# so far best overall tuning
results_warp.sort_values('precision', ascending=False).head(10)

factors  regularization  learning_rate  iterations  loss  max_sampled  \
63       64          0.0050          0.100          15  warp           50   
6        64          0.0001          0.010          15  warp           40   
19       64          0.0005          0.005          15  warp           50   
7        64          0.0001          0.010          15  warp           50   
39       64          0.0010          0.010          15  warp           50   
35       64          0.0010          0.005          15  warp           50   
18       64          0.0005          0.005          15  warp           40   
37       64          0.0010          0.010          15  warp           30   
20       64          0.0005          0.010          15  warp           20   
55       64          0.0050          0.010          15  warp           50   

    precision       map      ndcg       auc       mpr              uf_name  \
63     0.4400  0.303339  0.466041  0.512107  0.180783                 None   
6      0.4375  0.286728  0.450776  0.512616  0.113669        userf_country   
19     0.4375  0.296153  0.452041  0.511596  0.116191                userf   
7      0.4350  0.300020  0.464530  0.512347  0.112574                 None   
39     0.4325  0.302378  0.463361  0.511696  0.111476                 None   
35     0.4300  0.298488  0.470415  0.512124  0.113475  userf_country_brand   
18     0.4275  0.288300  0.454774  0.511596  0.114116                userf   
37     0.4275  0.292887  0.452743  0.512188  0.109535          userf_brand   
20     0.4250  0.295609  0.446397  0.511722  0.109251          userf_brand   
55     0.4250  0.295673  0.452581  0.512038  0.112946                 None   

              if_name  
63  itemf_group2_move  
6   itemf_group2_move  
19         itemf_cost  
7               itemf  
39  itemf_group2_move  
35              itemf  
18  itemf_group2_move  
37  itemf_group2_move  
20  itemf_group2_move  
55  itemf_group2_move

Trying to find a lower factor or iteration number for more efficient tuning using the parameters of the so far best model:

In [47]:
space_FM_warp = {'factors' : [10, 20, 30, 40, 50, 60, 70], 'regularization' : [0.0001], 'learning_rate' : [0.01], 'iterations' : [2, 4, 6, 8, 10, 12, 14, 16], 
'loss' : ['warp'], 'max_sampled' : [50]}

uf_combi = [userf_country]
if_combi = [itemf_group2_move]

uf_names = ['userf_country']
if_names = ['itemf_group2_move']

In [48]:
results_warp_pretuning = cv.tune_FM(space=space_FM_warp, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [36]:
results_warp_pretuning

factors  regularization  learning_rate  iterations  loss  max_sampled  \
0        10           0.005            0.1           2  warp           50   
1        10           0.005            0.1           4  warp           50   
2        10           0.005            0.1           6  warp           50   
3        10           0.005            0.1           8  warp           50   
4        10           0.005            0.1          10  warp           50   
5        10           0.005            0.1          20  warp           50   
6        10           0.005            0.1          40  warp           50   
7        10           0.005            0.1          16  warp           50   
8        20           0.005            0.1           2  warp           50   
9        20           0.005            0.1           4  warp           50   
10       20           0.005            0.1           6  warp           50   
11       20           0.005            0.1           8  warp           50   
12       20           0.005            0.1          10  warp           50   
13       20           0.005            0.1          20  warp           50   
14       20           0.005            0.1          40  warp           50   
15       20           0.005            0.1          16  warp           50   
16       30           0.005            0.1           2  warp           50   
17       30           0.005            0.1           4  warp           50   
18       30           0.005            0.1           6  warp           50   
19       30           0.005            0.1           8  warp           50   
20       30           0.005            0.1          10  warp           50   
21       30           0.005            0.1          20  warp           50   
22       30           0.005            0.1          40  warp           50   
23       30           0.005            0.1          16  warp           50   
24       40           0.005            0.1           2  warp           50   
25       40           0.005            0.1           4  warp           50   
26       40           0.005            0.1           6  warp           50   
27       40           0.005            0.1           8  warp           50   
28       40           0.005            0.1          10  warp           50   
29       40           0.005            0.1          20  warp           50   
30       40           0.005            0.1          40  warp           50   
31       40           0.005            0.1          16  warp           50   
32       50           0.005            0.1           2  warp           50   
33       50           0.005            0.1           4  warp           50   
34       50           0.005            0.1           6  warp           50   
35       50           0.005            0.1           8  warp           50   
36       50           0.005            0.1          10  warp           50   
37       50           0.005            0.1          20  warp           50   
38       50           0.005            0.1          40  warp           50   
39       50           0.005            0.1          16  warp           50   
40       60           0.005            0.1           2  warp           50   
41       60           0.005            0.1           4  warp           50   
42       60           0.005            0.1           6  warp           50   
43       60           0.005            0.1           8  warp           50   
44       60           0.005            0.1          10  warp           50   
45       60           0.005            0.1          20  warp           50   
46       60           0.005            0.1          40  warp           50   
47       60           0.005            0.1          16  warp           50   
48       70           0.005            0.1           2  warp           50   
49       70           0.005            0.1           4  warp           50   
50       70           0.005            0.1           6  warp           50   


In [37]:
from visualize_py import Visualize

In [38]:
vis = Visualize('science')

In [49]:
get_convergence_curves(results_warp_pretuning)

In [46]:
get_convergence_curves(results_warp_pretuning)

In [42]:
def get_convergence_curves(result_frame, save=False):

    from matplotlib import pyplot as plt
    # data preparation
    p_df = result_frame.pivot(index='iterations', columns='factors', values='precision')
    map_df = result_frame.pivot(index='iterations', columns='factors', values='map')
    ndcg_df = result_frame.pivot(index='iterations', columns='factors', values='ndcg')
    mpr_df = result_frame.pivot(index='iterations', columns='factors', values='mpr')
    data_df = [p_df, map_df, ndcg_df, mpr_df]
    names = ['P@10', 'MAP@10', 'NDCG@10', 'MPR']

    # plotting of the four curves
    fig, ax = plt.subplots(figsize=(17, 15), nrows=2, ncols=2)
    plt.subplots_adjust(wspace=0.2, hspace=0.3, right=0.82)
    c = 0
    for i in range(2):
        for j in range(2):
            data_filtered = data_df[c]
            ax[i,j].plot(data_filtered, linestyle='-', marker='o', linewidth=2)
            ax[i,j].set_title(names[c], fontsize=30)
            ax[i,j].set_xlabel('Iterations', fontsize=25)
            ax[i,j].tick_params(axis='both', which='major', labelsize=17)
            ax[i,j].tick_params(axis='both', which='minor', labelsize=17)
            #ax[i,j].autoscale()
            ax[i,j].grid(linestyle=':')
            c += 1
    fig.legend(data_filtered.columns, loc='center right', ncol=1, title='Factors',fancybox=True, shadow=False, frameon=True, title_fontsize=25, fontsize=20,
    bbox_to_anchor=(0.94, 0.79))
    if save:
        plt.savefig('curves.pdf')
    plt.show()

Trying computation time differences for lower factors and iterations:

In [50]:
space_FM_warp_low = {'factors' : [40], 'regularization' : [0.0001], 'learning_rate' : [0.01], 'iterations' : [10], 
'loss' : ['warp'], 'max_sampled' : [50]}

space_FM_warp_high = {'factors' : [64], 'regularization' : [0.0001], 'learning_rate' : [0.01], 'iterations' : [15], 
'loss' : ['warp'], 'max_sampled' : [50]}

uf_combi = [userf]
if_combi = [itemf]

uf_names = ['userf']
if_names = ['itemf']

In [51]:
results_warp_low = cv.tune_FM(space=space_FM_warp_low, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [52]:
results_warp_high = cv.tune_FM(space=space_FM_warp_high, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

Computation time halved!

Now tuning with lower factors and iterations:

In [53]:
space_FM_warp = {'factors' : [40], 'regularization' : [0.001, 0.005, 0.01], 
'learning_rate' : [0.05, 0.1, 0.5], 'iterations' : [10], 'loss' : ['warp'], 'max_sampled' : [40, 50, 60]}

uf_combi = [None, userf_country, userf_brand, userf_curr, userf_country_brand, userf_country_curr, userf_brand_curr, userf]
if_combi = [None, itemf_group2, itemf_move, itemf_cost, itemf_group2_move, itemf_group2_cost, itemf_move_cost, itemf]

uf_names = ['None', 'userf_country', 'userf_brand', 'userf_curr', 'userf_country_brand', 'userf_country_curr', 'userf_brand_curr', 'userf']
if_names = ['None', 'itemf_group2', 'itemf_move', 'itemf_cost', 'itemf_group2_move', 'itemf_group2_cost', 'itemf_move_cost', 'itemf']

In [54]:
results_warp = cv.tune_FM(space=space_FM_warp, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [60]:
results_warp.sort_values('precision', ascending=False).head(10)

factors  regularization  learning_rate  iterations  loss  max_sampled  \
13       40           0.005           0.10          10  warp           50   
21       40           0.010           0.10          10  warp           40   
23       40           0.010           0.10          10  warp           60   
18       40           0.010           0.05          10  warp           40   
14       40           0.005           0.10          10  warp           60   
22       40           0.010           0.10          10  warp           50   
23       40           0.010           0.10          10  warp           60   
19       40           0.010           0.05          10  warp           50   
22       40           0.010           0.10          10  warp           50   
23       40           0.010           0.10          10  warp           60   

    precision       map      ndcg       auc       mpr             uf_name  \
13     0.4450  0.313352  0.473037  0.512972  0.172204                None   
21     0.4400  0.325661  0.474465  0.511945  0.172450  userf_country_curr   
23     0.4325  0.283271  0.446177  0.512549  0.164250               userf   
18     0.4275  0.299535  0.463349  0.512685  0.130957                None   
14     0.4275  0.296621  0.449283  0.511720  0.172735                None   
22     0.4250  0.281903  0.438900  0.511350  0.173638  userf_country_curr   
23     0.4250  0.298159  0.455851  0.511893  0.147758    userf_brand_curr   
19     0.4225  0.280532  0.428532  0.510854  0.134053         userf_brand   
22     0.4175  0.302505  0.461669  0.511284  0.151899    userf_brand_curr   
23     0.4175  0.293889  0.442879  0.510851  0.148391    userf_brand_curr   

              if_name  
13  itemf_group2_move  
21              itemf  
23              itemf  
18              itemf  
14  itemf_group2_move  
22              itemf  
23  itemf_group2_move  
19         itemf_move  
22              itemf  
23              itemf

In [61]:
space_FM_warp_add = {'factors' : [40], 'regularization' : [0.05], 
'learning_rate' : [0.05, 0.1, 0.5], 'iterations' : [10], 'loss' : ['warp'], 'max_sampled' : [40, 50, 60]}

uf_combi = [None, userf_country, userf_brand, userf_curr, userf_country_brand, userf_country_curr, userf_brand_curr, userf]
if_combi = [None, itemf_group2, itemf_move, itemf_cost, itemf_group2_move, itemf_group2_cost, itemf_move_cost, itemf]

uf_names = ['None', 'userf_country', 'userf_brand', 'userf_curr', 'userf_country_brand', 'userf_country_curr', 'userf_brand_curr', 'userf']
if_names = ['None', 'itemf_group2', 'itemf_move', 'itemf_cost', 'itemf_group2_move', 'itemf_group2_cost', 'itemf_move_cost', 'itemf']

In [62]:
results_warp_add = cv.tune_FM(space=space_FM_warp_add, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [63]:
results_warp = pd.concat([results_warp, results_warp_add], axis=0)

In [64]:
results_warp.sort_values('precision', ascending=False).head(10)

factors  regularization  learning_rate  iterations  loss  max_sampled  \
13       40           0.005           0.10          10  warp           50   
21       40           0.010           0.10          10  warp           40   
23       40           0.010           0.10          10  warp           60   
18       40           0.010           0.05          10  warp           40   
14       40           0.005           0.10          10  warp           60   
22       40           0.010           0.10          10  warp           50   
23       40           0.010           0.10          10  warp           60   
19       40           0.010           0.05          10  warp           50   
22       40           0.010           0.10          10  warp           50   
23       40           0.010           0.10          10  warp           60   

    precision       map      ndcg       auc       mpr             uf_name  \
13     0.4450  0.313352  0.473037  0.512972  0.172204                None   
21     0.4400  0.325661  0.474465  0.511945  0.172450  userf_country_curr   
23     0.4325  0.283271  0.446177  0.512549  0.164250               userf   
18     0.4275  0.299535  0.463349  0.512685  0.130957                None   
14     0.4275  0.296621  0.449283  0.511720  0.172735                None   
22     0.4250  0.281903  0.438900  0.511350  0.173638  userf_country_curr   
23     0.4250  0.298159  0.455851  0.511893  0.147758    userf_brand_curr   
19     0.4225  0.280532  0.428532  0.510854  0.134053         userf_brand   
22     0.4175  0.302505  0.461669  0.511284  0.151899    userf_brand_curr   
23     0.4175  0.293889  0.442879  0.510851  0.148391    userf_brand_curr   

              if_name  
13  itemf_group2_move  
21              itemf  
23              itemf  
18              itemf  
14  itemf_group2_move  
22              itemf  
23  itemf_group2_move  
19         itemf_move  
22              itemf  
23              itemf

In [65]:
space_FM_warp_add = {'factors' : [40], 'regularization' : [0.001, 0.005, 0.01, 0.05], 
'learning_rate' : [0.05, 0.1, 0.5], 'iterations' : [10], 'loss' : ['warp'], 'max_sampled' : [30]}

uf_combi = [None, userf_country, userf_brand, userf_curr, userf_country_brand, userf_country_curr, userf_brand_curr, userf]
if_combi = [None, itemf_group2, itemf_move, itemf_cost, itemf_group2_move, itemf_group2_cost, itemf_move_cost, itemf]

uf_names = ['None', 'userf_country', 'userf_brand', 'userf_curr', 'userf_country_brand', 'userf_country_curr', 'userf_brand_curr', 'userf']
if_names = ['None', 'itemf_group2', 'itemf_move', 'itemf_cost', 'itemf_group2_move', 'itemf_group2_cost', 'itemf_move_cost', 'itemf']

In [66]:
results_warp_add = cv.tune_FM(space=space_FM_warp_add, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [67]:
results_warp = pd.concat([results_warp, results_warp_add], axis=0)

In [81]:
results_warp.sort_values('mpr', ascending=True).head(10)

factors  regularization  learning_rate  iterations  loss  max_sampled  \
6        40           0.010           0.05          10  warp           30   
3        40           0.005           0.05          10  warp           30   
6        40           0.010           0.05          10  warp           30   
18       40           0.010           0.05          10  warp           40   
6        40           0.010           0.05          10  warp           30   
9        40           0.005           0.05          10  warp           40   
20       40           0.010           0.05          10  warp           60   
10       40           0.005           0.05          10  warp           50   
18       40           0.010           0.05          10  warp           40   
20       40           0.010           0.05          10  warp           60   

    precision       map      ndcg       auc       mpr              uf_name  \
6      0.4325  0.292376  0.446305  0.512151  0.127441                 None   
3      0.3250  0.204083  0.346735  0.508168  0.128406                 None   
6      0.4100  0.245383  0.410180  0.511208  0.128686          userf_brand   
18     0.3550  0.216411  0.368861  0.509113  0.129612  userf_country_brand   
6      0.3375  0.207616  0.350448  0.508070  0.129756  userf_country_brand   
9      0.3300  0.212999  0.350195  0.508301  0.130177                 None   
20     0.3825  0.259216  0.406896  0.510042  0.130270  userf_country_brand   
10     0.3300  0.203823  0.330290  0.507660  0.130597                 None   
18     0.4150  0.284158  0.446045  0.511370  0.130597          userf_brand   
20     0.4000  0.272680  0.433817  0.512110  0.130701                 None   

         if_name  
6          itemf  
3   itemf_group2  
6     itemf_move  
18  itemf_group2  
6   itemf_group2  
9   itemf_group2  
20  itemf_group2  
10  itemf_group2  
18    itemf_move  
20         itemf

In [88]:
space_FM_warp_add = {'factors' : [40], 'regularization' : [0.001, 0.005, 0.01, 0.05], 
'learning_rate' : [0.05, 0.1, 0.5], 'iterations' : [10], 'loss' : ['warp'], 'max_sampled' : [20]}

uf_combi = [None, userf_country, userf_brand, userf_curr, userf_country_brand, userf_country_curr, userf_brand_curr, userf]
if_combi = [None, itemf_group2, itemf_move, itemf_cost, itemf_group2_move, itemf_group2_cost, itemf_move_cost, itemf]

uf_names = ['None', 'userf_country', 'userf_brand', 'userf_curr', 'userf_country_brand', 'userf_country_curr', 'userf_brand_curr', 'userf']
if_names = ['None', 'itemf_group2', 'itemf_move', 'itemf_cost', 'itemf_group2_move', 'itemf_group2_cost', 'itemf_move_cost', 'itemf']

In [89]:
results_warp_add = cv.tune_FM(space=space_FM_warp_add, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [90]:
results_warp = pd.concat([results_warp, results_warp_add], axis=0)

In [13]:
space_FM_warp_test = {'factors' : [40], 'regularization' : [0.005], 
'learning_rate' : [0.1], 'iterations' : [10], 'loss' : ['warp'], 'max_sampled' : [50]}

uf_combi = [None]
if_combi = [itemf_group2_move]

uf_names = ['None']
if_names = ['itemf_group2_move']

In [14]:
results_warp_test = cv.tune_FM(space=space_FM_warp_test, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [15]:
results_warp_test

factors  regularization  learning_rate  iterations  loss  max_sampled  \
0       40           0.005            0.1          10  warp           50   

   precision       map      ndcg       auc     mpr uf_name            if_name  
0     0.4225  0.290987  0.450773  0.511521  0.1793    None  itemf_group2_move

In [112]:
for uf in uf_names:
    for i_f in if_names:
        op = results_warp[(results_warp.uf_name==uf)&(results_warp.if_name==i_f)].sort_values('precision', ascending=False).head(1)
        if uf == 'None' and i_f == 'None':
            top_per_feature = op.copy()
        else:
            top_per_feature = pd.concat([top_per_feature, op], axis=0)
        

In [119]:
results_warp[(results_warp.uf_name=='userf_country_curr')&(results_warp.if_name=='itemf')].sort_values('precision', ascending=False).head()

factors  regularization  learning_rate  iterations  loss  max_sampled  \
21       40            0.01            0.1          10  warp           40   
22       40            0.01            0.1          10  warp           50   
23       40            0.01            0.1          10  warp           60   
7        40            0.01            0.1          10  warp           30   
7        40            0.01            0.1          10  warp           20   

    precision       map      ndcg       auc       mpr             uf_name  \
21     0.4400  0.325661  0.474465  0.511945  0.172450  userf_country_curr   
22     0.4250  0.281903  0.438900  0.511350  0.173638  userf_country_curr   
23     0.4125  0.285726  0.440104  0.512091  0.179172  userf_country_curr   
7      0.4100  0.285740  0.441768  0.510923  0.167337  userf_country_curr   
7      0.4075  0.287369  0.430853  0.511096  0.165549  userf_country_curr   

   if_name  
21   itemf  
22   itemf  
23   itemf  
7    itemf  
7    itemf

In [114]:
top_per_feature.pivot(index='uf_name', columns='if_name', values='precision')

if_name                None   itemf  itemf_cost  itemf_group2  \
uf_name                                                         
None                 0.2800  0.4325      0.3775        0.3550   
userf                0.3700  0.4325      0.3650        0.3500   
userf_brand          0.3550  0.4150      0.3650        0.3575   
userf_brand_curr     0.3500  0.4175      0.3575        0.3800   
userf_country        0.2675  0.3450      0.3350        0.3550   
userf_country_brand  0.3475  0.4000      0.3800        0.3825   
userf_country_curr   0.3475  0.4400      0.3575        0.3650   
userf_curr           0.2925  0.4125      0.3625        0.3725   

if_name              itemf_group2_cost  itemf_group2_move  itemf_move  \
uf_name                                                                 
None                            0.3650             0.4450      0.4100   
userf                           0.3950             0.4150      0.3600   
userf_brand                     0.3600             0.3900      0.4225   
userf_brand_curr                0.3975             0.4250      0.4025   
userf_country                   0.3775             0.4025      0.3925   
userf_country_brand             0.3450             0.3825      0.3825   
userf_country_curr              0.3600             0.3650      0.4000   
userf_curr                      0.3750             0.4025      0.4100   

if_name              itemf_move_cost  
uf_name                               
None                          0.4050  
userf                         0.3950  
userf_brand                   0.3750  
userf_brand_curr              0.4150  
userf_country                 0.4125  
userf_country_brand           0.4250  
userf_country_curr            0.3650  
userf_curr                    0.3925

In [111]:
for uf in uf_names:
    for i_f in if_names:
        if uf == 'None' and i_f == 'None':
            print(uf)
            print(i_f)

None
None


In [107]:
results_warp[(results_warp.uf_name=='None')&(results_warp.if_name=='None')].sort_values('precision', ascending=False).head(1)

factors  regularization  learning_rate  iterations  loss  max_sampled  \
1       40           0.001           0.05          10  warp           50   

   precision       map      ndcg       auc       mpr uf_name if_name  
1       0.28  0.148195  0.286833  0.508595  0.213471    None    None

Now tune BPR loss models:

In [77]:
space_FM_bpr = {'factors' : [40], 'regularization' : [0.001, 0.005, 0.01], 
'learning_rate' : [0.01, 0.05, 0.1], 'iterations' : [10], 'loss' : ['bpr'], 'max_sampled' : [1]}

uf_combi = [None, userf_country, userf_brand, userf_curr, userf_country_brand, userf_country_curr, userf_brand_curr, userf]
if_combi = [None, itemf_group2, itemf_move, itemf_cost, itemf_group2_move, itemf_group2_cost, itemf_move_cost, itemf]

uf_names = ['None', 'userf_country', 'userf_brand', 'userf_curr', 'userf_country_brand', 'userf_country_curr', 'userf_brand_curr', 'userf']
if_names = ['None', 'itemf_group2', 'itemf_move', 'itemf_cost', 'itemf_group2_move', 'itemf_group2_cost', 'itemf_move_cost', 'itemf']

In [78]:
results_bpr = cv.tune_FM(space=space_FM_bpr, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [80]:
results_bpr.sort_values('mpr', ascending=True).head(10)

factors  regularization  learning_rate  iterations loss  max_sampled  \
1       40           0.001           0.05          10  bpr            1   
1       40           0.001           0.05          10  bpr            1   
1       40           0.001           0.05          10  bpr            1   
1       40           0.001           0.05          10  bpr            1   
0       40           0.001           0.01          10  bpr            1   
1       40           0.001           0.05          10  bpr            1   
1       40           0.001           0.05          10  bpr            1   
0       40           0.001           0.01          10  bpr            1   
0       40           0.001           0.01          10  bpr            1   
0       40           0.001           0.01          10  bpr            1   

   precision       map      ndcg       auc       mpr           uf_name  \
1     0.2550  0.141409  0.273022  0.507202  0.104139              None   
1     0.2725  0.134807  0.269027  0.507060  0.105132              None   
1     0.2650  0.146232  0.281878  0.507409  0.107148              None   
1     0.3075  0.173261  0.319161  0.507898  0.108988              None   
0     0.2400  0.124324  0.249034  0.505683  0.109473             userf   
1     0.2675  0.154103  0.293901  0.507696  0.110027              None   
1     0.2700  0.136692  0.278959  0.507377  0.110099              None   
0     0.1975  0.099486  0.214491  0.505657  0.110164             userf   
0     0.2425  0.133427  0.273370  0.507287  0.110962  userf_brand_curr   
0     0.2125  0.101572  0.229643  0.505529  0.110966  userf_brand_curr   

             if_name  
1              itemf  
1  itemf_group2_move  
1  itemf_group2_cost  
1       itemf_group2  
0              itemf  
1    itemf_move_cost  
1         itemf_cost  
0  itemf_group2_move  
0  itemf_group2_move  
0              itemf

In [83]:
space_FM_bpr_add = {'factors' : [40], 'regularization' : [0.0005], 
'learning_rate' : [0.01, 0.05, 0.1], 'iterations' : [10], 'loss' : ['bpr'], 'max_sampled' : [1]}

uf_combi = [None, userf_country, userf_brand, userf_curr, userf_country_brand, userf_country_curr, userf_brand_curr, userf]
if_combi = [None, itemf_group2, itemf_move, itemf_cost, itemf_group2_move, itemf_group2_cost, itemf_move_cost, itemf]

uf_names = ['None', 'userf_country', 'userf_brand', 'userf_curr', 'userf_country_brand', 'userf_country_curr', 'userf_brand_curr', 'userf']
if_names = ['None', 'itemf_group2', 'itemf_move', 'itemf_cost', 'itemf_group2_move', 'itemf_group2_cost', 'itemf_move_cost', 'itemf']

In [84]:
results_bpr_add = cv.tune_FM(space=space_FM_bpr_add, user_f=uf_combi, item_f=if_combi, uf_names=uf_names, if_names=if_names, train=cal_w, 
test=val_w, exclude=test_w)

In [85]:
results_bpr = pd.concat([results_bpr, results_bpr_add], axis=0)

In [87]:
results_bpr.sort_values('mpr', ascending=True).head(10)

factors  regularization  learning_rate  iterations loss  max_sampled  \
1       40          0.0010           0.05          10  bpr            1   
1       40          0.0005           0.05          10  bpr            1   
1       40          0.0005           0.05          10  bpr            1   
1       40          0.0010           0.05          10  bpr            1   
1       40          0.0005           0.05          10  bpr            1   
1       40          0.0005           0.05          10  bpr            1   
1       40          0.0010           0.05          10  bpr            1   
1       40          0.0010           0.05          10  bpr            1   
0       40          0.0005           0.01          10  bpr            1   
0       40          0.0010           0.01          10  bpr            1   

   precision       map      ndcg       auc       mpr uf_name  \
1     0.2550  0.141409  0.273022  0.507202  0.104139    None   
1     0.2700  0.156089  0.293850  0.507304  0.104282    None   
1     0.2600  0.136159  0.265025  0.506721  0.104620    None   
1     0.2725  0.134807  0.269027  0.507060  0.105132    None   
1     0.2475  0.130434  0.265882  0.506915  0.106064    None   
1     0.2725  0.143808  0.282722  0.507257  0.106255    None   
1     0.2650  0.146232  0.281878  0.507409  0.107148    None   
1     0.3075  0.173261  0.319161  0.507898  0.108988    None   
0     0.2375  0.124910  0.247752  0.505598  0.109298   userf   
0     0.2400  0.124324  0.249034  0.505683  0.109473   userf   

             if_name  
1              itemf  
1              itemf  
1  itemf_group2_move  
1  itemf_group2_move  
1  itemf_group2_cost  
1       itemf_group2  
1  itemf_group2_cost  
1       itemf_group2  
0              itemf  
0              itemf

In [47]:
results_df_tuned_warp.to_csv('fm_tuning_warp_t.csv')

In [4]:
#results_df_tuned = pd.read_csv('fm_tuning_t.csv')